In [ ]:
# 🔧 Install required packages
!pip install -q sentence-transformers faiss-cpu
!pip install httpx
!pip install groq

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 130.2/130.2 kB 8.2 MB/s eta 0:00:00


In [ ]:

passages = [
    "Neural networks are computing systems inspired by the human brain. They consist of layers of nodes, or neurons, which can learn complex patterns.",
    "Transfer learning is a technique where a model trained on one task is reused on a second related task.",
    "Attention mechanisms allow models to focus on different parts of input data when making decisions, which improves performance in tasks like translation and summarization.",
    "Retrieval-augmented generation combines vector search with language models to answer questions from external documents.",
    "Convolutional Neural Networks are especially effective for image classification and computer vision tasks."
]

In [ ]:
from sentence_transformers import SentenceTransformer
import faiss
import numpy as np
import json

In [ ]:
# load the model
model = SentenceTransformer("all-MiniLM-L6-v2")

modules.json:   0%|          | 0.00/349 [00:00<?, ?B/s]

config_sentence_transformers.json:   0%|          | 0.00/116 [00:00<?, ?B/s]

README.md:   0%|          | 0.00/10.5k [00:00<?, ?B/s]

sentence_bert_config.json:   0%|          | 0.00/53.0 [00:00<?, ?B/s]

config.json:   0%|          | 0.00/612 [00:00<?, ?B/s]

...

tokenizer_config.json:   0%|          | 0.00/350 [00:00<?, ?B/s]

vocab.txt:   0%|          | 0.00/232k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/466k [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/112 [00:00<?, ?B/s]

config.json:   0%|          | 0.00/190 [00:00<?, ?B/s]

In [ ]:
# Generate vector embeddings
embeddings = model.encode(passages, convert_to_numpy=True)

In [ ]:
embeddings.shape

(5, 384)

In [ ]:
# Build FAISS index
index = faiss.IndexFlatL2(embeddings.shape[1])  # 384-dim

In [ ]:
index.add(embeddings)

# Save passage text and embeddings (we'll use them in the next step)
passage_store = {
    "passages": passages,
    "embedding_dim": embeddings.shape[1]
}

In [ ]:
# Sample query
query = "How do models use context when translating sentences?"

# Embed the query
query_vec = model.encode([query])[0]

In [ ]:
query_vec = np.array([query_vec])  # shape (1, 384)

In [ ]:
# Search top-3 most similar passages
D, I = index.search(query_vec, k=3)

In [ ]:
# Show results
print(" Query:", query)
print("\nTop Matches:")
retrieved_passages = []
for i in I[0]:
    retrieved_passages.append(passages[i])

In [ ]:
import os
from groq import Groq

In [ ]:
os.environ["GROQ_API_KEY"] = "API KEY"

In [ ]:
GROQ_MODEL = "llama3-8b-8192"

In [ ]:
def init_groq(api_key: str = None):
    api_key = api_key or os.getenv("GROQ_API_KEY")
    return Groq(api_key=api_key)


In [ ]:
def groq_chat(prompt: str, model_id: str, temperature: float = 0.7, max_tokens: int = 200):
    client = init_groq()
    response = client.chat.completions.create(
        model=model_id,
        messages=[
            {"role" : "system", "content" : "You are a helpful assistant."},
            {"role": "user", "content": prompt}
        ],
        temperature=temperature,
        max_tokens=max_tokens
    )
    return response.choices[0].message.content


In [ ]:
query = "What is attention mechanism?"
context = "\n".join(retrieved_passages)
prompt = f"""Use the following context to answer the question.

Context:
{context}

Question: {query}
Answer:"""

answer = groq_chat(prompt, model_id="llama3-8b-8192")
print(answer)


According to the provided context, an attention mechanism allows models to focus on different parts of input data when making decisions, which improves performance in tasks like translation and summarization.
